# UV-Grid Statistics

In [1]:
import numpy as np

import dask
import dask.array as da

from compute_uv_bins import load_ms_file
import groupby_apply

In [2]:
ds_ind, uvbins = load_ms_file('/scratch/users/jbochenek/data/1491550051.ms/', fieldid=3)

Selected column CHAN_FREQ from SPECTRAL_WINDOW with units Hz


In [3]:
ds_ind

<xarray.Dataset>
Dimensions:  (corr: 4, newrow: 172130304, uvw: 2)
Coordinates:
    U_bins   (newrow) int64 dask.array<chunksize=(10000000,), meta=np.ndarray>
    V_bins   (newrow) int64 dask.array<chunksize=(10000000,), meta=np.ndarray>
  * newrow   (newrow) MultiIndex
  - row      (newrow) int64 0 0 0 0 0 0 ... 42023 42023 42023 42023 42023 42023
  - chan     (newrow) int64 0 1 2 3 4 5 6 ... 4089 4090 4091 4092 4093 4094 4095
Dimensions without coordinates: corr, uvw
Data variables:
    DATA     (newrow, corr) complex64 dask.array<chunksize=(10000000, 4), meta=np.ndarray>
    UV       (newrow, uvw) float64 dask.array<chunksize=(10000000, 2), meta=np.ndarray>

---

### Dask Delayed Preparation

In [4]:
# Get dask arrays of UV-bins and visibilities from XArray dataset
dd_ubins = da.from_array(ds_ind.U_bins)
dd_vbins = da.from_array(ds_ind.V_bins)
dd_vals = da.from_array(ds_ind.DATA[:,0]+ds_ind.DATA[:,3])

In [5]:
dd_vals = da.from_array(ds_ind.DATA[:,0]+ds_ind.DATA[:,3])

In [6]:
# Combine U and V bins into one dask array
dd_bins = da.stack([dd_ubins, dd_vbins]).T
dd_bins

dask.array<transpose, shape=(172130304, 2), dtype=int64, chunksize=(10000000, 1), chunktype=numpy.ndarray>

In [7]:
# Apply unifrom chunks to both dask arrays
chunk_size = 10**7
dd_bins = dd_bins.rechunk([chunk_size, 2])
dd_vals = dd_vals.rechunk([chunk_size, 1])

In [8]:
# Convert to delayed data structures
bin_partitions = dd_bins.to_delayed()
val_partitions = dd_vals.to_delayed()

### Apply group-apply- to get bin indicies

Obtain a set of amplitude values for each bin in the UV-grid, returned to the notebook as the `value_groups` variable.

In [9]:
value_group_chunks = [dask.delayed(groupby_apply.group_bin_values_wrap)(part[0][0], part[1]) for part in zip(bin_partitions, val_partitions)]

In [10]:
value_groups_ = dask.delayed(groupby_apply.combine_group_values)(value_group_chunks)

In [11]:
# Compute the grid from above without doing the combine step
%time value_groups = value_groups_.compute()

CPU times: user 10min 7s, sys: 50.7 s, total: 10min 57s
Wall time: 17min 49s


---
## Create UV-bin Plot

In [13]:
from bokeh.plotting import figure, show, output_file

In [14]:
from bokeh.models import Label

In [15]:
from bokeh.layouts import gridplot 

In [16]:
from bokeh.io import output_notebook
output_notebook()

Loading BokehJS ...

In [12]:
# UV-grid bin count
len(value_groups), len(value_groups[0])

(214, 230)

In [109]:
# Look at bin contents and select some bins to plot
ubin_number = 131
selbins = []
for i, r_ in enumerate(value_groups[ubin_number]):
    if (len(r_) > 1100) and (len(r_) < 20000):
        bin_mean = np.median(r_)
        bin_mean = np.mean(r_)
        bin_max = np.max(r_)
#         if bin_max < 5:
        print(f'({ubin_number}, {i}):\t {len(r_)}\t{bin_mean:.2f}\t{bin_max:.2f}')
        selbins.append((ubin_number, i))

print( f"\nBins Selected: {len(selbins)}")

(131, 52):	 1861	0.17	0.83
(131, 53):	 4090	0.31	3.14
(131, 54):	 8891	0.32	4.16
(131, 55):	 11897	0.40	108.62
(131, 56):	 15425	0.52	81.15
(131, 57):	 15810	1.21	100.14
(131, 58):	 15981	4.50	257.50
(131, 59):	 16273	6.85	243.78
(131, 60):	 16442	9.25	376.03
(131, 61):	 16669	10.61	382.52
(131, 62):	 16932	6.28	389.07
(131, 63):	 17255	5.89	464.95
(131, 64):	 17462	0.62	11.37
(131, 65):	 17604	0.59	11.86
(131, 66):	 17801	0.62	15.78
(131, 67):	 18050	0.89	15.04
(131, 68):	 18261	1.22	13.99
(131, 69):	 18308	1.53	48.46
(131, 70):	 18347	1.60	63.37
(131, 71):	 18509	1.64	15.08
(131, 72):	 18621	1.64	16.98
(131, 73):	 18726	1.08	16.20
(131, 74):	 18764	0.77	13.03
(131, 75):	 18860	0.79	14.64
(131, 76):	 19104	0.79	39.62
(131, 77):	 19343	3.80	1169.08
(131, 78):	 19295	0.78	2.70
(131, 79):	 18766	9.11	4509.45
(131, 80):	 17225	39.20	12818.48
(131, 81):	 15540	10.43	2518.41
(131, 82):	 14033	14.29	14708.93
(131, 83):	 7131	78.35	12246.93
(131, 132):	 2610	32.41	1055.33
(131, 133):	 3986	12

In [110]:
print( f"\nBins Selected: {len(selbins[::2])}")


Bins Selected: 40


In [18]:
def make_hist_plot(binname, bin_values, nbins):
    '''Make a histogram plot of one bin in the UV grid.
    
    Parameters
    ----------
    binname : string
        Name to print on sub-plot to identify bin.
    bin_values : list-like
        List of bin values for the bin.
    nbins : int
        Number of bins for the histogram
        
    Returns
    -------
    p : bokeh.plotting.figure.Figure
        Figure to be shown or included in multi-plot
    '''
    
    hist, edges = np.histogram(bin_values, density=True, bins=nbins)
    p = figure(title=f'{binname}', tools='')
    p.quad(bottom=0, top=hist, left=edges[:-1], right=edges[1:], fill_color='navy', alpha=0.7)
    
    bin_mean = np.mean(bin_values)
    bin_mean_var = np.var(bin_values)

    bin_med = np.median(bin_values)
    bin_med_var = np.mean(abs(bin_values - bin_med)**2)    
    bin_ratio = bin_mean / bin_med

    mean_text = Label(x=60, y=125, x_units='screen', y_units='screen', text_font_size = "10px", text=f"mean : {bin_mean:.1f}±{bin_mean_var:.1f}")
    med_text = Label(x=60, y=115, x_units='screen', y_units='screen', text_font_size = "10px", text=f"med:   {bin_med:.1f}±{bin_med_var:.1f}")
    ratio_text = Label(x=60, y=105, x_units='screen', y_units='screen', text_font_size = "10px", text=f"ratio: {bin_ratio:.1f}")
    
    p.add_layout(mean_text)
    p.add_layout(med_text)
    p.add_layout(ratio_text)
    
    return p

In [114]:
# Plot some of the bins selected above
nbins = 100
plots = []
for sb in selbins[1::2]:
    bin_count = len(value_groups[sb[0]][sb[1]])
    bin_name = f"{sb} - {bin_count}"
#     print(f"Bin Name: {bin_name}")
    plots.append( make_hist_plot(bin_name, value_groups[sb[0]][sb[1]], nbins) )
print(len(plots))

40


In [115]:
# Plot a sample of bins and their amplitude distributions
show(gridplot(plots, ncols=5, plot_width=200, plot_height=200, toolbar_location=None))

---

---
## Plot and Fit a Bin

In [121]:
from scipy.optimize import curve_fit

In [136]:
from scipy.stats import norm, gamma, chi2
import matplotlib.mlab as mlab
import matplotlib.pyplot as plt

### Plot a bin with signal only

In [370]:
uvbin = (131, 145)
nbins = 200
bin_values = value_groups[uvbin[0]][uvbin[1]]

In [371]:
n, bins = np.histogram(bin_values, nbins, density=False)

In [372]:
scale = np.diff(bins)[0]*np.sum(n)

In [373]:
binscenters = np.array([0.5 * (bins[i] + bins[i+1]) for i in range(len(bins)-1)])

In [374]:
params = gamma.fit(bin_values)

In [375]:
params

(4.840597061036155, -0.18293320190811577, 0.22037973340384914)

In [376]:
y = scale*gamma.pdf(binscenters, *params)

In [377]:
TOOLS="hover,crosshair,pan,wheel_zoom,zoom_in,zoom_out,box_zoom,undo,redo,reset,tap,save,box_select,poly_select,lasso_select,"
p = figure(title=f'{uvbin}', tools=TOOLS, plot_width=800, plot_height=500)

#histogram
p.quad(bottom=0, top=n, left=bins[:-1], right=bins[1:], fill_color='navy', alpha=0.7)

#pdf function fit
p.line(binscenters, y, line_color='red', line_dash='5', line_width=2)

#print statistics on plot
bin_mean, bin_med = np.mean(bin_values), np.median(bin_values)
bin_mean_var, bin_med_var = np.var(bin_values), np.mean(abs(bin_values - bin_med)**2)
bin_ratio = bin_mean / bin_med

mean_text = Label(x=550, y=400, x_units='screen', y_units='screen', text=f"mean: {bin_mean:.1f} ± {bin_mean_var:.1f}")
med_text = Label(x=550, y=380, x_units='screen', y_units='screen', text=f"median: {bin_med:.1f} ± {bin_med_var:.1f}")
ratio_text = Label(x=550, y=360, x_units='screen', y_units='screen', text=f"ratio: {bin_ratio:.1f}")

p.add_layout(mean_text)
p.add_layout(med_text)
p.add_layout(ratio_text)

show(p)

---

### Plot a bin with signal and noise

In [378]:
uvbin = (107, 134)
nbins = 200
bin_values = value_groups[uvbin[0]][uvbin[1]]

In [379]:
bin_values_low = bin_values[np.where(bin_values<25)]

def fit_function(x, A, beta, B, mu, sigma):
    return (A * np.exp(-x/beta) + B * np.exp(-1.0 * (x - mu)**2 / (2 * sigma**2)))

def fit_function_1(x, A, beta):
    return (A * np.exp(-x/beta) )

def fit_function_2(x, B, mu, sigma):
    return ( B * np.exp(-1.0 * (x - mu)**2 / (2 * sigma**2) ) )

In [380]:
n, bins = np.histogram(bin_values_low, nbins, density=False)

In [381]:
binscenters = np.array([0.5 * (bins[i] + bins[i+1]) for i in range(len(bins)-1)])

In [382]:
popt, pcov = curve_fit(fit_function, xdata=binscenters, ydata=n, p0=[10, 8.0, 1000, 1., 0.8])
print(popt)

[2.18006012e+02 1.22900458e+01 8.77656410e+02 1.02677233e+00
 5.80766175e-01]


In [383]:
xspace = np.linspace(0, bins[-1], 1000)

In [384]:
y = fit_function(xspace, *popt)
y1 = fit_function_1(xspace, *popt[:2])
y2 = fit_function_2(xspace, *popt[2:])

In [385]:
TOOLS="hover,crosshair,pan,wheel_zoom,zoom_in,zoom_out,box_zoom,undo,redo,reset,tap,save,box_select,poly_select,lasso_select,"
p = figure(title=f'{uvbin}', tools=TOOLS, plot_width=800, plot_height=500)

#histogram
p.quad(bottom=0, top=n, left=bins[:-1], right=bins[1:], fill_color='navy', alpha=0.7)

#pdf function fit

p.line(xspace, y1, line_color='orange', line_width=2)
p.line(xspace, y2, line_color='green', line_width=2)
p.line(xspace, y, line_color='red', line_dash='5', line_width=2)

show(p)

---

## Plot UV-Stats

#### Compute the mean and median of each data point

In [321]:
from bokeh.plotting import ColumnDataSource

In [391]:
# Get dask arrays from XArray dataset
uval = ds_ind.UV[:,0]
vval = ds_ind.UV[:,1]

ubin = ds_ind.U_bins
vbin = ds_ind.V_bins

In [392]:
# Take a random sample of visibilities for plotting
n = 100000
x = np.random.choice(len(uval.data.flatten()), n)

In [393]:
# Sorting the sample indicies makes the following much faster
x.sort()

In [394]:
# Get dask arrays from XArray dataset then flatten from 82144 x 4096 to 1 dimension then take the sample
u = uval.data.flatten()[x]
v = vval.data.flatten()[x]

u_bins = ubin.data.flatten()[x]
v_bins = vbin.data.flatten()[x]

In [395]:
u = u.compute().squeeze()
v = v.compute().squeeze()

u_bins = u_bins.compute().squeeze()
v_bins = v_bins.compute().squeeze()

In [396]:
uv_colors = [
    "#%02x%02x%02x" % (int(r), int(g), 150) for r, g in zip(50+200*x/np.max(x), 30+200*x/np.max(x))
]

In [397]:
source = ColumnDataSource(data=dict(x=u, y=v, ubin=u_bins, vbin=v_bins, colors=uv_colors)) # 

In [398]:
# Bokeh plot for 2D scatter plot 
#      The color represents the order in the observation where later 
#      visibilities have lighter color to show georotational interferometery

TOOLS="hover,crosshair,pan,wheel_zoom,zoom_in,zoom_out,box_zoom,undo,redo,reset,tap,save,box_select,poly_select,lasso_select,"

TOOLTIPS = [
    ("index", "$index"),
    ("(x,y)", "($x{%0.1f}, $y{%0.1f})"),
    ("(u_bin, v_bin)", "(@ubin, @vbin)")
]

p = figure(tools=TOOLS, tooltips=TOOLTIPS)

p.scatter(x='x', y='y', fill_color='colors', fill_alpha=0.7, line_color=None, source=source)

# Draw a diagonal line
p.ray(x=[0, 0], y=[0, 0], length=0, angle=[np.pi/4., 5*np.pi/4.], color='black', line_dash='dashed', line_alpha=0.75)

GlyphRenderer(id='327711', ...)

In [399]:
show(p)

## Plot UV-Stats

#### Compute and plot the mean and median statistics of each bin

In [51]:
bin_stats = []

for i, u_groups in enumerate(value_groups):
    u_stats = []
    for k, bin_values in enumerate(u_groups):
        bin_mean, bin_med, bin_var, bin_ratio = 0, 0, 0, 0
        bin_count = len(bin_values)    
        if bin_count:
            bin_mean, bin_med = np.mean(bin_values), np.median(bin_values)
            bin_var = np.var(bin_values)
            bin_ratio = bin_mean / bin_med
            bin_max = np.max(bin_values)
        u_stats.append(np.array([int(i), int(k), bin_count, bin_mean, bin_med, bin_var, bin_ratio, bin_max]))
    bin_stats.append(np.array(u_stats))
bin_stats = np.array(bin_stats)

In [60]:
x_bin_range = bin_stats[:,:,0]
y_bin_range = bin_stats[:,:,1]

In [61]:
bin_max_values = bin_stats[:,:,7].flatten()
bin_mean_values = bin_stats[:,:,3].flatten()
bin_median_values = bin_stats[:,:,4].flatten()

#### Make a plot of the uv-grid colored by median fit with rfi-identified points highlighted

In [116]:
# Compute color scale to show median values
bin_max = 2. 
value_colors = [
    "#%02x%02x%02x" % (int(r), int(g), 150) for r, g in zip(50+200*bin_median_values/bin_max, 30+200*bin_median_values/bin_max)
]
value_colors = np.array(value_colors)

In [118]:
# Erase all bins with no data
value_colors[np.where(bin_median_values==0)] = "#FFFFFF"

In [117]:
# Black out all bins with "noise" (this is a naive criteria to detect RMS but it works approximately)
value_colors[np.where(bin_median_values>2.)] = "#000000"

In [389]:
p = figure(plot_width=1000, plot_height=1000, x_axis_label="U bins", y_axis_label="V bins")
p.rect(x_bin_range.flatten(), y_bin_range.flatten(), width=0.8, height=0.8, color=value_colors)
show(p)

**Caption**: This plot shows the median of each UV bin colored by median. The color 
scale is from purple to yellow where purple is lower value.  Bins with 
abnormally high median are colored in black. 

---